##### Copyright 2021 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# TFLite 创作工具

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/lite/guide/authoring"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a>
</td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/lite/guide/authoring.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 中运行</a></td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/lite/guide/authoring.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 GitHub 上查看源代码</a>
</td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/lite/guide/authoring.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a>   </td>
</table>

TensorFlow Lite Authoring API 提供了一种方式来维护与 TensorFlow Lite 兼容的 `tf.function` 模型。


## 安装

In [2]:
import tensorflow as tf

2023-11-07 21:48:11.853226: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-07 21:48:11.853276: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-07 21:48:11.855004: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## TensorFlow 到 TensorFlow Lite 的兼容性问题

如果您想在设备端使用您的 TF 模型，您需要将其转换为 TFLite 模型，以便从 TFLite 解释器使用它。在转换过程中，您可能会遇到兼容性错误，因为 TFLite 内置运算集不支持 TensorFlow 运算。

这是一个令人讨厌的问题。如何能够更早地检测到该问题呢，比如在模型创作时间？

请注意，以下代码将在调用 `converter.convert()` 时失败。


In [3]:
@tf.function(input_signature=[
    tf.TensorSpec(shape=[None], dtype=tf.float32)
])
def f(x):
  return tf.cosh(x)

# Evaluate the tf.function
result = f(tf.constant([0.0]))
print (f"result = {result}")

result = [1.]


In [4]:
# Convert the tf.function
converter = tf.lite.TFLiteConverter.from_concrete_functions(
    [f.get_concrete_function()], f)
try:
  fb_model = converter.convert()
except Exception as e:
  print(f"Got an exception: {e}")

Got an exception: Could not translate MLIR to FlatBuffer. UNKNOWN: /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py:695:1: error: 'tf.Cosh' op is neither a custom op nor a flex op
    self._concrete_variable_creation_fn = tracing_compilation.trace_function(
^
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:178:1: note: called from
    concrete_function = _maybe_define_function(
^
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:283:1: note: called from
        concrete_function = _create_concrete_function(
^
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:310:1: note: called from
  traced_func_graph = func_graph_module.func_graph_from_py_func(
^
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/p

2023-11-07 21:48:16.310019: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2023-11-07 21:48:16.310058: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.
Summary on the non-converted ops:
---------------------------------
 * Accepted dialects: tfl, builtin, func
 * Non-Converted Ops: 1, Total Ops 4, % non-converted = 25.00 %
 * 1 TF ops




- tf.Cosh:    1 occurrences  (f32: 1)
loc(fused["Cosh:", callsite("Cosh"("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py":695:1) at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":178:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":283:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflo

hon/eager/polymorphic_function/polymorphic_function.py":598:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/autograph_util.py":41:1 at callsite("/tmpfs/tmp/ipykernel_34429/885400331.py":5:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/weak_tensor_ops.py":88:1 at "/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/gen_math_ops.py":2612:1)))))))))]): error: 'tf.Cosh' op is neither a custom op nor a flex op
error: failed while converting: 'main': 
Some ops are not supported by the native TFLite runtime, you can enable TF kernels fallback using TF Select. See instructions: https://www.tensorflow.org/lite/guide/ops_select 
TF Select ops: Cosh
Details:
	tf.Cosh(tensor<?xf32>) -> (tensor<?xf32>) : {device = ""}



## 简单的目标感知创作用法

我们引入了 Authoring API 来检测模型创作期间的 TensorFlow Lite 兼容性问题。

您只需添加 `@tf.lite.experimental.authoring.compatible` 修饰器来封装您的 `tf.function` 模型，以检查 TFLite 兼容性。

之后，当您评估模型时，将自动检查兼容性。

In [5]:
@tf.lite.experimental.authoring.compatible
@tf.function(input_signature=[
    tf.TensorSpec(shape=[None], dtype=tf.float32)
])
def f(x):
  return tf.cosh(x)

# Evaluate the tf.function
result = f(tf.constant([0.0]))
print (f"result = {result}")


COMPATIBILITY WARNING: op 'tf.Cosh' require(s) "Select TF Ops" for model conversion for TensorFlow Lite. https://www.tensorflow.org/lite/guide/ops_select
Op: tf.Cosh
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/gen_math_ops.py:2612
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/weak_tensor_ops.py:88
  - /tmpfs/tmp/ipykernel_34429/885400331.py:5
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/autograph_util.py:41
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py:598
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/framework/func_graph.py:1059
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:310
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compi

2023-11-07 21:48:16.415556: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2023-11-07 21:48:16.415597: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.
Summary on the non-converted ops:
---------------------------------
 * Accepted dialects: tfl, builtin, func
 * Non-Converted Ops: 1, Total Ops 4, % non-converted = 25.00 %
 * 1 TF ops




- tf.Cosh:    1 occurrences  (f32: 1)
loc(fused["Cosh:", callsite("Cosh"("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py":695:1) at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":178:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":283:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflo

如果发现任何 TensorFlow Lite 兼容性问题，它将显示 `COMPATIBILITY WARNING` 或 `COMPATIBILITY ERROR` 以及有问题的运算的确切位置。在本例中，它显示了 tf.unction 模型中 `tf.Cosh` 运算的位置。

您还可以使用 `<function_name>.get_compatibility_log()` 方法检查兼容性日志。

In [6]:
compatibility_log = '\n'.join(f.get_compatibility_log())
print (f"compatibility_log = {compatibility_log}")

compatibility_log = COMPATIBILITY WARNING: op 'tf.Cosh' require(s) "Select TF Ops" for model conversion for TensorFlow Lite. https://www.tensorflow.org/lite/guide/ops_select
Op: tf.Cosh
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/gen_math_ops.py:2612
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/weak_tensor_ops.py:88
  - /tmpfs/tmp/ipykernel_34429/885400331.py:5
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/autograph_util.py:41
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py:598
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/framework/func_graph.py:1059
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:310
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_fu

## 引发不兼容性异常

您可以为 `@tf.lite.experimental.authoring.compatible` 修饰器提供一个选项。当您尝试评估经过修饰的模型时，`raise_exception` 选项会引发异常。

In [7]:
@tf.lite.experimental.authoring.compatible(raise_exception=True)
@tf.function(input_signature=[
    tf.TensorSpec(shape=[None], dtype=tf.float32)
])
def f(x):
  return tf.cosh(x)

# Evaluate the tf.function
try:
  result = f(tf.constant([0.0]))
  print (f"result = {result}")
except Exception as e:
  print(f"Got an exception: {e}")

COMPATIBILITY WARNING: op 'tf.Cosh' require(s) "Select TF Ops" for model conversion for TensorFlow Lite. https://www.tensorflow.org/lite/guide/ops_select
Op: tf.Cosh
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/gen_math_ops.py:2612
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/ops/weak_tensor_ops.py:88
  - /tmpfs/tmp/ipykernel_34429/885400331.py:5
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/autograph_util.py:41
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py:598
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/framework/func_graph.py:1059
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:310
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compi

2023-11-07 21:48:16.539202: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2023-11-07 21:48:16.539249: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.


Summary on the non-converted ops:
---------------------------------
 * Accepted dialects: tfl, builtin, func
 * Non-Converted Ops: 1, Total Ops 4, % non-converted = 25.00 %
 * 1 TF ops




- tf.Cosh:    1 occurrences  (f32: 1)
loc(fused["Cosh:", callsite("Cosh"("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py":695:1) at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":178:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":283:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py":310:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/framework/func_graph.py":1059:1 at callsite("/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/pyt

## 指定 "Select TF ops" 用法

如果您已了解 [Select Tf op](https://tensorflow.google.cn/lite/guide/ops_select) 用法，可以通过设置 `converter_target_spec` 将其用于 Authoring API。它与您将在 [tf.lite.TFLiteConverter](https://tensorflow.google.cn/api_docs/python/tf/lite/TFLiteConverter) API 中使用的对象相同。


In [8]:
target_spec = tf.lite.TargetSpec()
target_spec.supported_ops = [
    tf.lite.OpsSet.TFLITE_BUILTINS,
    tf.lite.OpsSet.SELECT_TF_OPS,
]
@tf.lite.experimental.authoring.compatible(converter_target_spec=target_spec, raise_exception=True)
@tf.function(input_signature=[
    tf.TensorSpec(shape=[None], dtype=tf.float32)
])
def f(x):
  return tf.cosh(x)

# Evaluate the tf.function
result = f(tf.constant([0.0]))
print (f"result = {result}")


result = [1.]


2023-11-07 21:48:16.665435: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2023-11-07 21:48:16.665473: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.
Summary on the non-converted ops:
---------------------------------
 * Accepted dialects: tfl, builtin, func
 * Non-Converted Ops: 1, Total Ops 4, % non-converted = 25.00 %
 * 1 TF ops




- tf.Cosh:    1 occurrences  (f32: 1)
2023-11-07 21:48:16.680080: W tensorflow/compiler/mlir/lite/flatbuffer_export.cc:2921] TFLite interpreter needs to link Flex delegate in order to run the model since it contains the following Select TFop(s):
Flex ops: FlexCosh
Details:
	tf.Cosh(tensor<?xf32>) -> (tensor<?xf32>) : {device = ""}
See instructions: https://www.tensorflow.org/lite/guide/ops_select


## 检查 GPU 兼容性

如果您希望确保您的模型与 TensorFlow Lite 的 [GPU 委托](https://tensorflow.google.cn/lite/performance/gpu)兼容，您可以设置 [tf.lite.TargetSpec](https://tensorflow.google.cn/api_docs/python/tf/lite/TargetSpec) 的 `experimental_supported_backends`。

以下示例展示如何确保您的模型的 GPU 委托兼容性。请注意，此模型存在兼容性问题，因为它使用带有 tf.slice 算子和不受支持的 tf.cosh 算子的二维张量。您将看到两个带有位置信息的 `COMPATIBILITY WARNING`。

In [9]:
target_spec = tf.lite.TargetSpec()
target_spec.supported_ops = [
    tf.lite.OpsSet.TFLITE_BUILTINS,
    tf.lite.OpsSet.SELECT_TF_OPS,
]
target_spec.experimental_supported_backends = ["GPU"]
@tf.lite.experimental.authoring.compatible(converter_target_spec=target_spec)
@tf.function(input_signature=[
    tf.TensorSpec(shape=[4, 4], dtype=tf.float32)
])
def func(x):
  y = tf.cosh(x)
  return y + tf.slice(x, [1, 1], [1, 1])

result = func(tf.ones(shape=(4,4), dtype=tf.float32))

'tfl.slice' op is not GPU compatible: SLICE supports for 3 or 4 dimensional tensors only, but node has 2 dimensional tensors.
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/util/dispatch.py:1260
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/util/traceback_utils.py:150
  - /tmpfs/tmp/ipykernel_34429/3833138856.py:13
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/autograph_util.py:41
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/polymorphic_function.py:598
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/framework/func_graph.py:1059
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:310
  - /tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/python/eager/polymorphic_function/tracing_compilation.py:283
  - /tmpfs/src/tf_docs_en

2023-11-07 21:48:16.820800: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2023-11-07 21:48:16.820846: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.
Summary on the non-converted ops:
---------------------------------
 * Accepted dialects: tfl, builtin, func
 * Non-Converted Ops: 2, Total Ops 7, % non-converted = 28.57 %
 * 1 ARITH ops, 1 TF ops

- arith.constant:    1 occurrences  (i32: 1)



- tf.Cosh:    1 occurrences  (f32: 1)
  (f32: 1)
  (f32: 1)
2023-11-07 21:48:16.837705: W tensorflow/compiler/mlir/lite/flatbuffer_export.cc:2921] TFLite interpreter needs to link Flex delegate in order to run the model since it contains the following Select TFop(s):
Flex ops: FlexCosh
Details:
	tf.Cosh(tensor<4x4xf32>) -> (tensor<4x4xf32>) : {device = ""}
See instructions: https://www.tensorflow.org/lite/guide/ops_select
loc(fused["Cosh:", callsite("Cosh"("/tmpfs/src/tf_docs_env/lib/python

## 阅读更多

有关更多信息，请参阅：

- [tf.function](https://tensorflow.google.cn/api_docs/python/tf/function) API 文档
- [使用 tf.function 提升性能](https://tensorflow.google.cn/guide/function)
- [TensorFlow Lite Converter](https://tensorflow.google.cn/lite/models/convert)
- [TensorFlow Lite Model Analyzer](https://tensorflow.google.cn/lite/guide/model_analyzer)
- [TensorFlow Lite GPU 委托](https://tensorflow.google.cn/lite/performance/gpu)